# Test Flickr API

In [121]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob
from pathlib import Path
import requests
import json
from pprint import pprint
from multiprocessing.pool import ThreadPool
import threading
import urllib.request
import hashlib

from tqdm import tqdm_notebook as tqdm
import pandas as pd
import numpy as np
from random import randint

import sys
sys.path.append('/work/megapixels_dev/megapixels')
from app.utils import api_utils, identity_utils

from app.settings import app_cfg
from app.settings import types

import flickr_api  # pip install flickr_api
from flickr_api.flickrerrors import FlickrAPIError

## Create CSV for API

In [73]:
fp_in = '/data_store/datasets/people/pipa/downloads/annotations/index.txt'
fp_out = '/data_store_hdd/datasets/people/pipa/research/flickr_metadata/'
fp_out_photo_ids = '/data_store/datasets/people/pipa/research/pipa_photo_ids.csv'
fp_out_photoset_ids = '/data_store/datasets/people/pipa/research/pipa_photoset_ids.csv'

In [56]:
names = ['photoset_id', 'photo_id', 'xmin', 'ymin', 'height', 'identity_id', 'subset_id']
df_records = pd.read_csv(fp_in, delimiter=' ', names=names, index_col=False)
df_records.drop(['xmin', 'ymin', 'height', 'identity_id', 'subset_id'], axis=1, inplace=True)
records = df_records.to_dict('records')

```
<photoset_id> <photo_id> <xmin> <ymin> <width> <height> <identity_id> <subset_id>
The subset IDs are 0 for leftover, 1 for train, 2 for validation, 3 for test

The photos are located in the images directory, in the form <photoset_id>_<photo_id>.jpg
```

In [69]:
photo_ids = []
for record in records:
  fp = '{}.json'.format(record['photo_id'])
  photo_ids.append({'filepath': fp, 'query': record['photo_id']}) 
df_photo_ids = pd.DataFrame.from_dict(photo_ids)
df_photo_ids.to_csv(fp_out_photo_ids, index=False)

In [74]:
photoset_ids = []
for record in records:
  fp = '{}.json'.format(record['photoset_id'])
  photoset_ids.append({'filepath': fp, 'query': record['photoset_id']}) 
df_photoset_ids = pd.DataFrame.from_dict(photoset_ids)
df_photoset_ids.to_csv(fp_out_photoset_ids, index=False)

# Test Flickr API

In [64]:
FLICKR_API_KEY = '31cae6cbba7020585a34bf5fcd772e16'
FLICKR_API_SECRET = '4688b458314b2e09'

# init Flickr API
flickr_api.set_keys(api_key=FLICKR_API_KEY, api_secret=FLICKR_API_SECRET)

In [78]:
photo_id = records[0]['photo_id']
print(photo_id)
print(records[0]['photoset_id'])

1808093328
72157607317745768


In [103]:
photo = flickr_api.Photo(id=photo_id)
info = photo.getInfo()

In [67]:
from pprint import pprint

In [122]:
flickr_url = 'https://api.flickr.com/services/rest/?method=flickr.photos.getInfo&api_key=31cae6cbba7020585a34bf5fcd772e16&photo_id=6796778203&format=json&nojsoncallback=1'

In [125]:
from requests.compat import urljoin, quote_plus
url = "http://some-address.com/api/"
term = 'This is a test'
flickr_url = 'https://api.flickr.com/services/rest/?method=flickr.photos.getInfo&api_key=31cae6cbba7020585a34bf5fcd772e16&photo_id=6796778203&format=json&nojsoncallback=1'

urljoin(url, quote_plus(term))
                            

'http://some-address.com/api/This+is+a+test'

In [ ]:
from urllib.request.u

In [123]:
import urllib.request, json 
with urllib.request.urlopen(flickr_url) as url:
  data = json.loads(url.read().decode())
  print(data)

{'photo': {'id': '6796778203', 'secret': 'e2c0873305', 'server': '7033', 'farm': 8, 'dateuploaded': '1328033443', 'isfavorite': 0, 'license': '0', 'safety_level': '0', 'rotation': 0, 'owner': {'nsid': '62559061@N06', 'username': 'Joybot', 'realname': '', 'location': 'United Kingdom', 'iconserver': '4503', 'iconfarm': 5, 'path_alias': 'joybot'}, 'title': {'_content': 'Unfortunate hair thanks to sudden gust of wind and lack of hair straighteners'}, 'description': {'_content': 'I think this was before the time of widespread hair straighteners.\nWhat a wonderful modern world we now live in.\n\nPolhawn Fort, Cornwall, UK.\nFuji colour negative film, 100ISO, Kodak Box Brownie (620 format, cropped).'}, 'visibility': {'ispublic': 1, 'isfriend': 0, 'isfamily': 0}, 'dates': {'posted': '1328033443', 'taken': '2000-12-01 00:00:00', 'takengranularity': '4', 'takenunknown': 0, 'lastupdate': '1348236375'}, 'views': '438', 'editability': {'cancomment': 0, 'canaddmeta': 0}, 'publiceditability': {'canco

In [124]:
with open('/home/adam/Downloads/test.json', 'w') as fp:
  json.dump(data, fp)

In [119]:
pprint(info)

{'canaddmeta': 0,
 'canblog': 0,
 'cancomment': 1,
 'candownload': 1,
 'canprint': 0,
 'canshare': 1,
 'comments': '0',
 'dateuploaded': '1193821883',
 'description': 'Urmas Paet with Tallinn skyline as backdrop.',
 'editability': {'canaddmeta': 0, 'cancomment': 0},
 'farm': 3,
 'id': '1808093328',
 'isfamily': 0,
 'isfavorite': 0,
 'isfriend': 0,
 'ispublic': 1,
 'lastupdate': '1291726681',
 'license': '4',
 'media': 'photo',
 'notes': [],
 'originalformat': 'jpg',
 'originalsecret': '84b2933747',
 'owner_id': '16941867@N06',
 'owner_username': 'Estonian Foreign Ministry',
 'people': {'haspeople': 0},
 'posted': '1193821883',
 'rotation': 0,
 'safety_level': '0',
 'secret': '285209b709',
 'server': '2364',
 'tag_ids': ['16896545-1808093328-4053146',
             '16896545-1808093328-29495',
             '16896545-1808093328-77084',
             '16896545-1808093328-3363'],
 'tag_names': ['paet', 'foreign', 'minister', 'estonia'],
 'taken': '2007-10-18 16:01:14',
 'takengranularity': '